In [1]:
'''This code block sets the parameters for evaluating'''
P=32 #precision of L-function estimate
crit=9/4 #the real value of the critical line
delta=2 #delta, as given by Yoshida, far enough that crit+delta is in the region of absolute convergence of the series
Lerror=100

In [2]:
'''This code block defines the L function being considered and the associated gamma factors used to complete it'''
L=zeta
Gam(s)=pi^(-s/2)*gamma(s/2)

In [3]:
'''This code just defines some functions that are needed to compute variation of argument'''

def argbranch(z,t):
    '''this gives the branch of arg of z in the interval (t-pi,t+pi), might screw up on an edge case'''
    x=float(arg(z))
    if abs(x-t)<pi:
        return x
    else:
        n=floor(abs(x-t)/(2*pi))
        if x<t:
            return float(x+2*pi*(n+1))
        else:
            return float(x-2*pi*(n+1))

def argvarl(lcalcfile, path, n):
    '''lcalcfile is the name of an lcalc file and should be input as a string in quotation marks.  path is a list of complex points.  This function uses lcalc to compute the variation of the argument of f (divided by pi) on the straight line segments in CC connecting the points in path, estimated using n subdivisions each.  Should be used for the L function part of the variation of argument calculation'''
    
    # Make list of values of L using lcalc.  Format will be list of pairs (s, L(s))
    values=[]
    for i in range(0, len(path)-1):
        rawvaluesstr=lcalc('--value-line-segment -x'+str(path[i].real())+' -y'+str(path[i].imag())+' -X'+str(path[i+1].real())+' -Y'+str(path[i+1].imag())+' --number-samples='+str(n)+' -F'+str(lcalcfile)+'.txt')
        rawvalues0=rawvaluesstr.split()
        for j in range(len(rawvalues0)/4):
            values.append((float(rawvalues0[4*j])+I*float(rawvalues0[4*j+1]), float(rawvalues0[4*j+2])+I*float(rawvalues0[4*j+3])))
    lastvals=lcalc('-v -x'+str(path[len(path)-1].real())+' -y'+str(path[len(path)-1].imag())+' -F'+str(lcalcfile)+'.txt').split()
    values.append((path[len(path)-1],float(lastvals[0])+I*float(lastvals[1])))

    # Compute variation of the argument
    start=arg(values[0][1])
    t=start
    for k in range(len(values)):
        m=argbranch(values[k][1], t)
        t=m
    return t-start

In [4]:
def count_zeroes(lcalcfile, bleft, tright, n):
    '''Returns number of zeroes of function defined by lcalcfile.txt in the box with bottom left corner bleft and top right corner tright.  Precision is given by n, the number of steps taken along the path'''
    
    
    def delta_L(n):
        '''Estimates variation of argument for the L function'''
        return argvarl(lcalcfile, [bleft, bleft+(tright-bleft).real(), tright, tright-(tright-bleft).real(), bleft], n)
        
    return ((delta_L(n))/(2*pi)).n(P)

In [5]:
%%time
count_zeroes('g1_lcalcfile', .25+13.5*I, 1+15*I, 10)

CPU times: user 631 ms, sys: 418 ms, total: 1.05 s
Wall time: 2.67 s


0.000000000

In [6]:
def split_box(bleft, tright, hv):
    '''Cuts the box with bottom left corner bleft and top right corner tright into two boxes horizontally or vertically depending on hv.  hv will switch after cutting so the next split will go the opposite direction.  Always returns the bottom or left box.'''
    box=[]
    
    if hv==0: # 0 corresponds to cutting horizontally
        new_bleft=bleft
        new_tright=tright.real()+((bleft+tright)*1.0/2).imag()*I
    else: # cut vertically
        new_bleft=bleft
        new_tright=((bleft+tright)/2.0).real()+tright.imag()*I
        
    box=[new_bleft, new_tright, hv]    
    return box

In [7]:
def find_heights(bleft, tright, lcalcfile, prec):
    '''Finds heights of zeroes of function defined in lcalcfile.txt with mesh equal to prec in the box with bottom left corner bleft and top right corner tright.  Prints heights and returns heights in a list.  Estimates heights by middle (vertically) of horizontal strips.'''
    
    heights=[]
    actual_find(bleft, tright, lcalcfile, prec, heights)
    return heights

def actual_find(bleft, tright, lcalcfile, prec, heights):
    n=round(max(tright.imag()-bleft.imag(), tright.real()-bleft.real())*100)
    
    if count_zeroes(lcalcfile, bleft, tright, n)>0:
        if tright.imag()-bleft.imag()<prec:
        #    print (bleft.imag()+tright.imag())/2
            heights.append((bleft.imag()+tright.imag())/2)
    
        else:
            bottombox=split_box(bleft, tright, 0)
            topbox=[bottombox[1].imag()*I+bottombox[0].real(), bottombox[1].real()+(2*bottombox[1].imag()-bottombox[0].imag())*I, 0]
            actual_find(bottombox[0], bottombox[1], lcalcfile, prec, heights)
            actual_find(topbox[0], topbox[1], lcalcfile, prec, heights)

In [8]:
find_heights(.25+10*I, .75+30*I, 'g1_lcalcfile', .01)

[]

In [9]:
def find_real(bleft, tright, lcalcfile, prec):
    '''Finds real part of zeroes of function defined by lcalcfile.txt in a box with bottom left corner bleft and top right corner tright.  Mesh is given by prec.  Estimate of real part is given in the middle of the vertical strip.'''
    
    reals=[]
    actual_reals(bleft, tright, lcalcfile, prec, reals)
    return reals
    
def actual_reals(bleft, tright, lcalcfile, prec, reals):
    n=round(max(tright.real()-bleft.real(), tright.imag()-bleft.imag())*100)
    
    if count_zeroes(lcalcfile, bleft, tright, n)>0:
        if tright.real()-bleft.real() < prec:
         #   print (bleft.real()+tright.real())/2
            reals.append((tright.real()+bleft.real())/2)
            
        else:
            leftbox=split_box(bleft, tright, 1)
            rightbox=[leftbox[1].real()+leftbox[0].imag()*I, leftbox[1].real()*2-leftbox[0].real()+leftbox[1].imag()*I, 1]
            actual_reals(leftbox[0], leftbox[1], lcalcfile, prec, reals)
            actual_reals(rightbox[0], rightbox[1], lcalcfile, prec, reals)

In [10]:
find_real(.1+14*I, .9+30*I, 'g1_lcalcfile', .1)

[]

In [11]:
def find_zeroes(bleft, tright, lcalcfile, prec):
    '''Finds zeroes of function defined by lcalcfile.txt in the box with bottom left corner bleft and top right corner tright. prec sets the size of the mesh.  Estimate gives the middle of the box containing a zero.'''
    
    zeroes=[]
    heights=find_heights(bleft, tright, lcalcfile, prec)
    for i in range(len(heights)):
        temp_bleft=bleft.real()+(heights[i]-prec/2)*I
        temp_tright=tright.real()+(heights[i]+prec/2)*I
        realparts=find_real(temp_bleft, temp_tright, lcalcfile, prec)
        
        for j in range(len(realparts)):
            print heights[i]*I+realparts[j]
            zeroes.append(heights[i]*I+realparts[j])
            
    return zeroes

In [12]:
find_zeroes(10*I, 5+30*I, 'g1_lcalcfile', .1)

0.507812500000000 + 12.9296875000000*I


0.507812500000000 + 15.1171875000000*I


0.351562500000000 + 17.2265625000000*I


0.507812500000000 + 17.3046875000000*I


1.28906250000000 + 19.1796875000000*I


...

0.507812500000000 + 23.7109375000000*I


1.28906250000000 + 26.2890625000000*I
1.44531250000000 + 26.2890625000000*I


0.507812500000000 + 27.6953125000000*I


0.507812500000000 + 29.1796875000000*I


[0.507812500000000 + 12.9296875000000*I,
 0.507812500000000 + 15.1171875000000*I,
 0.351562500000000 + 17.2265625000000*I,
 0.507812500000000 + 17.3046875000000*I,
 1.28906250000000 + 19.1796875000000*I,
 0.507812500000000 + 21.9140625000000*I,
 0.507812500000000 + 23.7109375000000*I,
 1.28906250000000 + 26.2890625000000*I,
 1.44531250000000 + 26.2890625000000*I,
 0.507812500000000 + 27.6953125000000*I,
 0.507812500000000 + 29.1796875000000*I]

In [13]:
find_heights(10*I, 1.5 + 20*I, 'g1_lcalcfile', 0.3)

[12.8906250000000, 15.0781250000000, 17.2656250000000, 19.1406250000000]

In [14]:
find_heights(.49+8*I,2+150*I, 'g1_lcalcfile', 0.1)

[8.93603515625000,
 12.9575195312500,
 15.1069335937500,
 17.2563476562500,
 19.1977539062500,
 21.9018554687500,
 23.7045898437500,
 26.0620117187500,
 26.1313476562500,
 26.2006835937500,
 26.2700195312500,
 27.6567382812500,
 29.1127929687500,
 31.1235351562500,
 31.9555664062500,
 33.6196289062500,
 35.7690429687500,
 36.6010742187500,
 38.1264648437500,
 39.9291992187500,
 41.3852539062500,
 42.9799804687500,
 43.8120117187500,
 45.1987304687500,
 47.5561523437500,
 49.3588867187500,
 50.3989257812500,
 51.9936523437500,
 53.3803710937500,
 54.4204101562500,
 55.5297851562500,
 57.1245117187500,
 58.5112304687500,
 59.2739257812500,
 60.7993164062500,
 61.7006835937500,
 62.3247070312500,
 64.1967773437500,
 64.2661132812500,
 65.0981445312500,
 66.4155273437500,
 67.7329101562500,
 68.5649414062500,
 70.0903320312500,
 71.8237304687500,
 71.8930664062500,
 73.4877929687500,
 74.3891601562500,
 75.9145507812500,
 76.7465820312500,
 78.1333007812500,
 80.2133789062500,
 80.97607421

In [15]:
find_heights(.49+8*I,2+300*I, 'g1_lcalcfile', 0.1)

[26.2856445312500,
 27.7114257812500,
 29.1372070312500,
 31.1333007812500,
 31.9887695312500,
 33.6284179687500,
 35.6958007812500,
 35.7670898437500,
 36.6225585937500,
 38.1196289062500,
 39.9731445312500,
 41.3276367187500,
 43.0385742187500,
 43.8227539062500,
 45.1772460937500,
 47.6010742187500,
 49.3833007812500,
 50.3813476562500,
 52.0209960937500,
 53.3754882812500,
 54.4448242187500,
 55.5141601562500,
 57.1538085937500,
 58.5083007812500,
 59.2924804687500,
 60.7895507812500,
 61.7163085937500,
 62.3579101562500,
 71.9106445312500,
 73.4790039062500,
 74.4057617187500,
 75.9028320312500,
 76.6870117187500,
 78.1127929687500,
 80.1801757812500,
 80.2514648437500,
 80.9643554687500,
 82.1762695312500,
 82.2475585937500,
 82.3901367187500,
 84.1723632812500,
 85.4555664062500,
 86.4536132812500,
 87.5229492187500,
 88.8061523437500,
 89.7329101562500,
 89.8041992187500,
 90.8735351562500,
 91.5864257812500,
 93.0834960937500,
 93.8676757812500,
 94.4379882812500,
 95.86376953

In [16]:
find_heights(.49+150*I,2+300*I, 'g1_lcalcfile', 0.1)

[150.622558593750,
 152.087402343750,
 152.160644531250,
 153.479003906250,
 153.771972656250,
 154.870605468750,
 156.481933593750,
 156.701660156250,
 157.800292968750,
 158.679199218750,
 159.338378906250,
 160.363769531250,
 161.608886718750,
 162.341308593750,
 162.414550781250,
 162.487792968750,
 162.561035156250,
 162.634277343750,
 163.073730468750,
 163.659667968750,
 164.611816406250,
 165.783691406250,
 166.735839843750,
 167.761230468750,
 168.273925781250,
 168.933105468750,
 170.178222656250,
 170.764160156250,
 171.569824218750,
 172.155761718750,
 173.327636718750,
 173.620605468750,
 175.231933593750,
 175.891113281250,
 176.916503906250,
 177.722167968750,
 180.505371093750,
 180.578613281250,
 180.651855468750,
 180.725097656250,
 180.798339843750,
 182.043457031250,
 182.849121093750,
 184.240722656250,
 185.485839843750,
 186.291503906250,
 186.804199218750,
 187.683105468750,
 188.562011718750,
 189.733886718750,
 190.466308593750,
 190.539550781250,
 190.6127929